In [27]:
train_file ='train/in.tsv.xz'
test_file = 'test-A/in.tsv.xz'
out_file = 'test-A/out.tsv'

In [2]:
from itertools import islice
import regex as re
import sys
from torchtext.vocab import build_vocab_from_iterator
import lzma
import pickle
import re
import torch
from torch import nn
from torch.utils.data import IterableDataset
import itertools
from torch.utils.data import DataLoader
import yaml

In [3]:
epochs = 3
embed_size = 200
device = 'cuda'
vocab_size = 30000
batch_s = 1600
learning_rate = 0.01
k = 20 #top k words
wildcard_minweight = 0.02

In [4]:
params = yaml.load(open('config/params.yaml'))
#then, entire code should go about those params with params[epochs] etc

/tmp/ipykernel_30815/1141171476.py:1: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  params = yaml.load(open('config/params.yaml'))


In [5]:
params = {
'epochs': 3,
'embed_size': 300,
'device': 'cuda',
'vocab_size': 30000,
'batch_size': 3200,
'learning_rate': 0.001,
'k': 15, #top k words
'wildcard_minweight': 0.1
}

In [6]:
params

{'epochs': 3,
 'embed_size': 300,
 'device': 'cuda',
 'vocab_size': 30000,
 'batch_size': 3200,
 'learning_rate': 0.001,
 'k': 15,
 'wildcard_minweight': 0.1}

In [7]:
def get_words_from_line(line):
    line = line.rstrip()
    yield '<s>'
    line = preprocess(line)
    for t in line.split(' '):
        yield t
    yield '</s>'


def get_word_lines_from_file(file_name):
    n = 0
    with lzma.open(file_name, 'r') as fh:
        for line in fh:
            n+=1
            if n%1000==0:
                print(n)
            yield get_words_from_line(line.decode('utf-8'))


In [8]:
###preprocessing
def preprocess(line):
    line = get_rid_of_header(line)
    line = replace_endline(line)
    return line

def get_rid_of_header(line):
    line = line.split('\t')[6:]
    return " ".join(line)
    
def replace_endline(line):
    line = line.replace("\\n", " ")
    return line

In [9]:
def look_ahead_iterator(gen):
    prev2 = None
    prev1 = None
    for item in gen:
        if prev2 is not None and prev1 is not None:
            yield (prev2, prev1, item)
        prev2 = prev1
        prev1 = item

class Trigrams(IterableDataset):
  def __init__(self, text_file, vocabulary_size):
      self.vocab = build_vocab_from_iterator(
         get_word_lines_from_file(text_file),
         max_tokens = vocabulary_size,
         specials = ['<unk>'])
      self.vocab.set_default_index(self.vocab['<unk>'])
      self.vocabulary_size = vocabulary_size
      self.text_file = text_file

  def __iter__(self):
     return look_ahead_iterator(
         (self.vocab[t] for t in itertools.chain.from_iterable(get_word_lines_from_file(self.text_file))))
    

Vocab()

In [23]:
vocab = build_vocab_from_iterator(
    get_word_lines_from_file(train_file),
    max_tokens = params['vocab_size'],
    specials = ['<unk>'])

1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000
53000
54000
55000
56000
57000
58000
59000
60000
61000
62000
63000
64000
65000
66000
67000
68000
69000
70000
71000
72000
73000
74000
75000
76000
77000
78000
79000
80000
81000
82000
83000
84000
85000
86000
87000
88000
89000
90000
91000
92000
93000
94000
95000
96000
97000
98000
99000
100000
101000
102000
103000
104000
105000
106000
107000
108000
109000
110000
111000
112000
113000
114000
115000
116000
117000
118000
119000
120000
121000
122000
123000
124000
125000
126000
127000
128000
129000
130000
131000
132000
133000
134000
135000
136000
137000
138000
139000
140000
141000
142000
143000
144000
145000
146000
147000
148000
149000
150000
151000
152000
153000
154000
155000
156000
157000
158000
15

In [24]:
with open('filename.pickle', 'wb') as handle:
    pickle.dump(vocab, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [10]:
with open('filename.pickle','rb') as handle:
    vocab = pickle.load(handle)
    
train_dataset = Trigrams(train_file, params['vocab_size'])

1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000
53000
54000
55000
56000
57000
58000
59000
60000
61000
62000
63000
64000
65000
66000
67000
68000
69000
70000
71000
72000
73000
74000
75000
76000
77000
78000
79000
80000
81000
82000
83000
84000
85000
86000
87000
88000
89000
90000
91000
92000
93000
94000
95000
96000
97000
98000
99000
100000
101000
102000
103000
104000
105000
106000
107000
108000
109000
110000
111000
112000
113000
114000
115000
116000
117000
118000
119000
120000
121000
122000
123000
124000
125000
126000
127000
128000
129000
130000
131000
132000
133000
134000
135000
136000
137000
138000
139000
140000
141000
142000
143000
144000
145000
146000
147000
148000
149000
150000
151000
152000
153000
154000
155000
156000
157000
158000
15

In [11]:
data = DataLoader(train_dataset, batch_size=params['batch_size']) #load data 

In [27]:
print(type(data))

<class 'torch.utils.data.dataloader.DataLoader'>


In [33]:
class SimpleTrigramNeuralLanguageModel(nn.Module):
  def __init__(self, vocabulary_size, embedding_size):
      super(SimpleTrigramNeuralLanguageModel, self).__init__()
      self.embeddings = nn.Embedding(vocabulary_size, embedding_size)
      self.linear = nn.Linear(2*embedding_size, vocabulary_size)
      self.linear_matrix_2 = nn.Linear(embedding_size*2, embedding_size*2)
      self.relu = nn.ReLU()
      self.softmax = nn.Softmax()
    
    #for each word in vocabulary theres a separate embedding vector, consisting of embedding_size entries
    #self.linear is linear layer consisting of concatenated embeddings of left, and right context words
    #self.linear_matrix_2 is linear layer 
    
  def forward(self, x): #x is list of prev and following embeddings
      emb_left = self.embeddings(x[0])
      emb_right = self.embeddings(x[1])
        #create two embeddings vectors, for word before and after, respectively
    
      first_layer_size_2 = self.linear_matrix_2(torch.cat((emb_left, emb_right), dim=1))
      first_relu = self.relu(first_layer_size_2)
      concated = self.linear(first_relu)
      out = self.softmax(concated)
      return out

In [65]:
import gc
torch.cuda.empty_cache()
gc.collect()

0

In [39]:
device = 'cuda'
model = SimpleTrigramNeuralLanguageModel(params['vocab_size'], params['embed_size']).to(device)
optimizer = torch.optim.Adam(model.parameters(), lr=params['learning_rate'])
criterion = torch.nn.NLLLoss()

In [14]:
torch.autograd.set_detect_anomaly(True)
# model.load_state_dict(torch.load(f'model-tri-2following-final.bin'))
for i in range(params['epochs']):
    print('epoch: =', i)
    model.train()
    step = 0
    for x, y, z in data: # word, following, 2nd_following words
       x = x.to(device)
       y = y.to(device)
       z = z.to(device)
       optimizer.zero_grad()
       ypredicted = model([y, z]) #following, 2nd_following word
       loss = criterion(torch.log(ypredicted), x) #x is to_predict
       if step % 100 == 0:
          print(step, loss)
       step += 1
       if step % 10000 == 0:
                torch.save(model.state_dict(), f'model-tri-2following-embed=200steps-{step}.bin')    
       loss.backward()
       optimizer.step()
#     torch.save(model.state_dict(), f'model-tri-2following-{i}.bin')    

epoch: = 0
0 

/tmp/ipykernel_30815/606935597.py:22: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  out = self.softmax(concated)


tensor(10.3473, device='cuda:0', grad_fn=<NllLossBackward0>)
1000
100 tensor(6.4702, device='cuda:0', grad_fn=<NllLossBackward0>)
200 tensor(6.1728, device='cuda:0', grad_fn=<NllLossBackward0>)
2000
300 tensor(6.1315, device='cuda:0', grad_fn=<NllLossBackward0>)
3000
400 tensor(6.1413, device='cuda:0', grad_fn=<NllLossBackward0>)
4000
500 tensor(5.9379, device='cuda:0', grad_fn=<NllLossBackward0>)
5000
600 tensor(6.0123, device='cuda:0', grad_fn=<NllLossBackward0>)
6000
700 tensor(6.0021, device='cuda:0', grad_fn=<NllLossBackward0>)
7000
800 tensor(5.8060, device='cuda:0', grad_fn=<NllLossBackward0>)
8000
900 tensor(5.8374, device='cuda:0', grad_fn=<NllLossBackward0>)
9000
1000 tensor(5.7561, device='cuda:0', grad_fn=<NllLossBackward0>)
10000
1100 tensor(5.7806, device='cuda:0', grad_fn=<NllLossBackward0>)
11000
1200 tensor(5.9041, device='cuda:0', grad_fn=<NllLossBackward0>)
12000
1300 tensor(5.8457, device='cuda:0', grad_fn=<NllLossBackward0>)
13000
1400 tensor(5.9296, device='cuda:0

114000
11600 tensor(5.2242, device='cuda:0', grad_fn=<NllLossBackward0>)
115000
11700 tensor(5.4189, device='cuda:0', grad_fn=<NllLossBackward0>)
116000
11800 tensor(5.4812, device='cuda:0', grad_fn=<NllLossBackward0>)
117000
11900 tensor(5.5100, device='cuda:0', grad_fn=<NllLossBackward0>)
118000
12000 tensor(5.4680, device='cuda:0', grad_fn=<NllLossBackward0>)
119000
12100 tensor(5.4753, device='cuda:0', grad_fn=<NllLossBackward0>)
120000
12200 tensor(5.3741, device='cuda:0', grad_fn=<NllLossBackward0>)
121000
12300 tensor(5.2679, device='cuda:0', grad_fn=<NllLossBackward0>)
122000
12400 tensor(5.4868, device='cuda:0', grad_fn=<NllLossBackward0>)
123000
12500 tensor(5.2248, device='cuda:0', grad_fn=<NllLossBackward0>)
124000
12600 tensor(4.9390, device='cuda:0', grad_fn=<NllLossBackward0>)
125000
12700 tensor(5.2555, device='cuda:0', grad_fn=<NllLossBackward0>)


/home/gedin/.local/lib/python3.10/site-packages/torch/autograd/__init__.py:200: UserWarning: Error detected in LogBackward0. Traceback of forward call that caused the error:
  File "/usr/lib/python3.10/runpy.py", line 196, in _run_module_as_main
    return _run_code(code, main_globals, None,
  File "/usr/lib/python3.10/runpy.py", line 86, in _run_code
    exec(code, run_globals)
  File "/home/gedin/.local/lib/python3.10/site-packages/ipykernel_launcher.py", line 17, in <module>
    app.launch_new_instance()
  File "/home/gedin/.local/lib/python3.10/site-packages/traitlets/config/application.py", line 1043, in launch_instance
    app.start()
  File "/home/gedin/.local/lib/python3.10/site-packages/ipykernel/kernelapp.py", line 725, in start
    self.io_loop.start()
  File "/home/gedin/.local/lib/python3.10/site-packages/tornado/platform/asyncio.py", line 195, in start
    self.asyncio_loop.run_forever()
  File "/usr/lib/python3.10/asyncio/base_events.py", line 600, in run_forever
    sel

RuntimeError: Function 'LogBackward0' returned nan values in its 0th output.

In [15]:
torch.save(model.state_dict(),'model-tri-2following-embed=300.bin')

In [319]:
a = results[5]
print(a)

{'is': 0.11248013377189636, 'be': 0.0887126550078392, 'are': 0.05770659074187279, 'was': 0.04821299761533737, 'and': 0.031015213578939438, '<unk>': 0.02695723995566368, 'been': 0.016298962756991386, 'Is': 0.01539035513997078, 'not': 0.015107596293091774, 'were': 0.014968073926866055}


In [338]:
b={'is': 0.2, 'the': 0.2, '<unk>': 0.4}

In [324]:
b={'is': 0.2, 'the': 0.2}

In [328]:
results_summ = summarize_probs_unk(b, const_wildcard = False)

In [329]:
print(results_summ)

[('is', 0.25), ('the', 0.25), ('<unk>', 0.5)]


In [293]:
print(b)

{'is': 0.495, 'the': 0.495}


In [16]:
def get_first_word(text):
    """Return the first word of a string."""
    word = ""
    for i in range(len(text)-1):
#         if text[i] in [' ', ',', '.']
        if text[i] == ' ':
            return word.rstrip()
        else:
            word += text[i]
    return word.rstrip()

def get_values_from_model(context: list, model, vocab, k=10):
    words = [vocab.forward([word]) for word in context]
    ixs =  torch.tensor(words).to(device)
    out = model(ixs)
    top = torch.topk(out[0], k)
    top_indices = top.indices.tolist()
    top_probs = top.values.tolist()
    top_words = vocab.lookup_tokens(top_indices)
    return list(zip(top_words, top_probs))

def summarize_probs_unk(dic, const_wildcard=True):
    ''' 
    dic: dictionary of probabilities returned by model 
    returns: tab of probabilities, with <unk> specificly as last element
    '''
    if const_wildcard:  
        if '<unk>' in dic.keys():
            del dic['<unk>']
        probsum = sum(float(val) for key, val in dic.items())
        for key in dic:
            dic[key] = dic[key]/(probsum*(1+params['wildcard_minweight'])) ###leave some space for wildcard
        tab = [(key, val) for key, val in dic.items()]
        tab.append(('<unk>', 1-sum([val for val in dic.values()])))
    elif '<unk>' not in dic.keys():
        tab = [(key, val) for key, val in dic.items()]
        tab.append(('<unk>', 1-sum([val for val in dic.values()])))
    else:
        wildcard_value = dic['<unk>']
        del dic['<unk>']
        probsum = sum([float(val) for key, val in dic.items()])
        for key in dic:
            dic[key] = dic[key]/(probsum+wildcard_value)
        tab = [(key, val) for key, val in dic.items()]
        tab.append(('<unk>', 1-sum([val for val in dic.values()])))
    return tab

def gonito_format(dic, const_wildcard = True):
    tab = summarize_probs_unk(dic=dic, const_wildcard=const_wildcard)
    result = ''
    for element in tab[:-1]:
        result+=str(element[0])+':'+str(element[1])+'\t'
    result += ':'+ str(tab[-1][1]) + '\n'
    return result

In [19]:

ixs = torch.tensor([vocab.forward(['States']), vocab.forward(['of'])]).to(device)

out = model(ixs)
top = torch.topk(out[0], 10)
top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

/tmp/ipykernel_30815/606935597.py:22: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  out = self.softmax(concated)


[('the', 1, 0.28959694504737854),
 ('<unk>', 0, 0.2600848376750946),
 ('United', 157, 0.24865739047527313),
 ('loyal', 3181, 0.011600562371313572),
 ('ed', 193, 0.009287656284868717),
 ('other', 59, 0.009135955013334751),
 ('of', 2, 0.00894735287874937),
 ('Southern', 853, 0.007434409577399492),
 ('tho', 33, 0.00726652005687356),
 ('The', 17, 0.006302454508841038)]

In [40]:
model.load_state_dict(torch.load(f'model-tri-2following-embed=100.bin'))

<All keys matched successfully>

In [41]:
with lzma.open(test_file, 'rt') as file:
    predict_words = []
    results = []
    for line in file:
        line = replace_endline(line) #get only relevant
        line = line.split('\t')[6:]
        context = line[1].rstrip().split(" ")[:2] #two words from the left context
        predict_words.append(context) #get_first_word(split[1cd 
    vocab = train_dataset.vocab
    for context_words in predict_words:
        predicted_distribution = get_values_from_model(context_words, model, vocab, k=10)
        distribution_as_dict = dict(predicted_distribution)
#         print(distribution_as_dict)
        results.append(distribution_as_dict)


/tmp/ipykernel_30815/606935597.py:22: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  out = self.softmax(concated)


[{'<unk>': 0.22333872318267822, 'the': 0.04290543496608734, 'of': 0.038316406309604645, 'to': 0.03587133809924126, 'and': 0.03049224615097046, 'in': 0.015468255616724491, 'was': 0.012148280628025532, 'a': 0.011980442330241203, 'be': 0.011976692825555801, 'is': 0.010855000466108322}, {'<unk>': 0.21075238287448883, 'hundred': 0.0673641711473465, 'dred': 0.005059292074292898, 'eight': 0.004337533377110958, 'degrees': 0.0038635244127362967, 'due': 0.003796575590968132, 'dollars': 0.003567937295883894, 'long': 0.003466016612946987, 'north': 0.003463953034952283, 'men': 0.00341203180141747}, {'a': 0.16613157093524933, 'the': 0.15993879735469818, '<unk>': 0.0938526839017868, 'this': 0.019656965509057045, 'other': 0.01839813031256199, 'of': 0.015854211524128914, 'and': 0.014281678013503551, 'his': 0.012650839053094387, 'The': 0.01190563477575779, 'tho': 0.010437354445457458}, {'<unk>': 0.11687463521957397, 'it': 0.049038924276828766, 'they': 0.03917419910430908, 'and': 0.03811464458703995, 'wh

In [419]:
with open(out_file, 'w') as outfile:
    for elem in results:  
        outfile.write(gonito_format(elem, const_wildcard=False))

In [42]:
# torch.save(model.state_dict(), f'model-tri-2following-embed=100.bin')    
with open("test-A/out-embed100.tsv", 'w') as outfile:
    for elem in results:  
        outfile.write(gonito_format(elem, const_wildcard=False))


In [37]:
# torch.save(model.state_dict(), f'model-tri-2following-embed=200.bin')
with open('test-A/out-embed=200.tsv', 'w') as outfile:
    for elem in results:  
        outfile.write(gonito_format(elem, const_wildcard=False))

In [31]:
# torch.save(model.state_dict(), f'model-tri-2following-embed=300.bin')
with open('test-A/out-embed=300.tsv', 'w') as outfile:
    for elem in results:  
        outfile.write(gonito_format(elem, const_wildcard=False))

In [ ]:
#############Below is only testing, trying ################

In [357]:
results_summ = summarize_probs_unk(a, const_wildcard = False)

In [414]:
results_summ = [summarize_probs_unk(result, const_wildcard = False) for result in results]

In [412]:
results_summ

[[('and', 0.09401928299350774),
  ('was', 0.042643945320216904),
  ('out', 0.028740502993675726),
  ('that', 0.02787611493798393),
  ('placed', 0.02753900259090668),
  ('work', 0.026609481081919257),
  ('made', 0.02404004335064763),
  ('is', 0.023600215460896846),
  ('up', 0.022804205421178007),
  ('<unk>', 0.6821272058490673)],
 [('and', 0.14603855372856134),
  ('that', 0.03460113439693535),
  ('or', 0.03433247108224818),
  ('as', 0.03266713033798552),
  ('was', 0.0304657482478034),
  ('is', 0.026710330960551327),
  ('be', 0.026167258600020275),
  ('made', 0.02382438016840368),
  ('contained', 0.02104032870501253),
  ('<unk>', 0.6241526637724784)],
 [('the', 0.8654011008272448),
  ('tho', 0.037689351539917704),
  ('a', 0.0193492144333675),
  ('tbe', 0.014019879550277874),
  ('in', 0.010837857102072803),
  ('of', 0.008755495252329338),
  ('The', 0.008282891210957499),
  ('his', 0.007617956082930567),
  ('this', 0.007218053907233167),
  ('<unk>', 0.020828200093668814)],
 [('foreclosed',

In [415]:
for idx, element in enumerate(results_summ):
    print(idx, ': ', sum([float(entry[1]) for entry in element]))

0 :  1.0
1 :  1.0
2 :  1.0
3 :  1.0
4 :  1.0
5 :  1.0
6 :  1.0
7 :  1.0
8 :  1.0
9 :  1.0
10 :  1.0
11 :  1.0
12 :  1.0
13 :  1.0
14 :  1.0
15 :  1.0
16 :  1.0
17 :  1.0
18 :  1.0
19 :  1.0
20 :  1.0
21 :  1.0
22 :  1.0
23 :  1.0
24 :  1.0
25 :  1.0
26 :  1.0
27 :  1.0
28 :  1.0
29 :  1.0
30 :  1.0
31 :  1.0
32 :  1.0
33 :  1.0
34 :  1.0
35 :  1.0
36 :  1.0
37 :  1.0
38 :  1.0
39 :  1.0
40 :  1.0
41 :  1.0
42 :  1.0
43 :  1.0
44 :  1.0
45 :  1.0
46 :  1.0
47 :  1.0
48 :  1.0
49 :  1.0
50 :  1.0
51 :  1.0
52 :  1.0
53 :  1.0
54 :  1.0
55 :  1.0
56 :  1.0
57 :  1.0
58 :  1.0
59 :  1.0
60 :  1.0
61 :  1.0
62 :  1.0
63 :  1.0
64 :  1.0
65 :  1.0
66 :  1.0
67 :  1.0
68 :  1.0
69 :  1.0
70 :  1.0
71 :  1.0
72 :  1.0
73 :  1.0
74 :  1.0
75 :  1.0
76 :  1.0
77 :  1.0
78 :  1.0
79 :  1.0
80 :  1.0
81 :  1.0
82 :  1.0
83 :  1.0
84 :  1.0
85 :  1.0
86 :  1.0
87 :  1.0
88 :  1.0
89 :  1.0
90 :  1.0
91 :  1.0
92 :  1.0
93 :  1.0
94 :  1.0
95 :  1.0
96 :  1.0
97 :  1.0
98 :  1.0
99 :  1.0
100 :  1.0

In [346]:
tab = results_summ
result = ''
for element in tab[:-1]:
    result+=str(element[0])+':'+str(element[1])+'\t'
result += ':'+ str(tab[-1][1]) + '\n'
print(result, end='')

a:0.32235596453720317	the:0.29815671218498524	this:0.037712611177471045	other:0.03380747940487517	of:0.029858854655014522	and:0.027513870807796215	his:0.02489330633482702	The:0.022330998789039776	tho:0.01943313977820608	:0.18393706233058182


In [199]:
gonito_format(results[2], const_wildcard = False)

'a:0.3910634709171287\tthe:0.3617063481722642\tthis:0.04575074218211916\tother:0.041013263886742826\tof:0.03622302244589748\tand:0.033378224696135494\this:0.030199108590644053\tThe:0.027090666394293545\ttho:0.023575152714774474\t:0.01\n'

In [373]:
vocab.forward(['despicable'])

[0]

In [367]:
print(predict_words[1571])

['and', 'despicable']


In [366]:
print(predict_words[1902])

['and', 'Democratic,"']


In [368]:
print(predict_words[2281])

['and', 'ltiules,']


In [362]:
for elem in results:
    print(gonito_format(elem, const_wildcard=False), end='')

the:0.20759828216564447	of:0.18641195492052776	to:0.16375589974544083	and:0.14197683369027864	in:0.07235947734331608	a:0.058097948235152734	was:0.05579373084177645	be:0.05459636692777879	is:0.049409506130084366	:0.01
hundred:0.6757441672297902	dred:0.05507351954564639	eight:0.04366350604170377	degrees:0.04027646004808541	due:0.03587563285715766	north:0.03523299091044305	long:0.03521327274265904	men:0.035105103052205704	dollars:0.03381534757230843	:0.01
a:0.39106347091712873	the:0.36170634817226427	this:0.045750742182119164	other:0.04101326388674283	of:0.036223022445897486	and:0.033378224696135494	his:0.030199108590644057	The:0.02709066639429355	tho:0.023575152714774478	:0.01
it:0.1767555335571485	they:0.14081408629938671	and:0.1369251675661277	which:0.11277892922943726	he:0.10500778470392595	you:0.08516978500368706	It:0.08279808722888964	I:0.07644183587914447	who:0.07330879053225288	:0.01
able:0.16135098933162126	and:0.13044751689027728	order:0.12047644195204929	enough:0.11219570761860

In [98]:
entry = {'the': 0.10045935900113911, 'of': 0.09020703498174018, 'to': 0.07924349156201368, 'and': 0.0687043339508765, 'in': 0.035015639993431324, 'a': 0.02811431086085686, 'was': 0.026999271757820558, 'be': 0.026419852650704238, 'is': 0.023909866992206572}

In [100]:
summarize_probs_unk(entry, const_wildcard=False)

[('the', 0.2075982821656445),
 ('of', 0.18641195492052778),
 ('to', 0.16375589974544083),
 ('and', 0.14197683369027864),
 ('in', 0.07235947734331606),
 ('a', 0.05809794823515274),
 ('was', 0.055793730841776454),
 ('be', 0.054596366927778785),
 ('is', 0.04940950613008436),
 ('<unk>', 0.01)]

In [126]:
b = dict(get_values_from_model(['le', 'to'], model, vocab, k=10))

[('<unk>', 0.23124052584171295), ('and', 0.025475040078163147), ('to', 0.016587475314736366), ('will', 0.01190512627363205), ('not', 0.011148410849273205), ('I', 0.010462148115038872), ('the', 0.010157403536140919), ('would', 0.007865948602557182), ('he', 0.0076030828058719635), ('is', 0.007369522470980883)]


/tmp/ipykernel_4654/606935597.py:22: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  out = self.softmax(concated)


In [127]:
b

{'<unk>': 0.23124052584171295,
 'and': 0.025475040078163147,
 'to': 0.016587475314736366,
 'will': 0.01190512627363205,
 'not': 0.011148410849273205,
 'I': 0.010462148115038872,
 'the': 0.010157403536140919,
 'would': 0.007865948602557182,
 'he': 0.0076030828058719635,
 'is': 0.007369522470980883}